# FACIAL Quick Demo: train a new person

## 1. Clone FACIAL Github Repo

In [ ]:
%tensorflow_version 1.x

!git clone https://github.com/adiehl96/FACIAL.git

TensorFlow 1.x selected.
Cloning into 'FACIAL'...
remote: Enumerating objects: 978, done.
remote: Counting objects: 100% (978/978), done.
remote: Compressing objects: 100% (958/958), done.
remote: Total 978 (delta 99), reused 838 (delta 9), pack-reused 0
Receiving objects: 100% (978/978), 9.40 MiB | 17.17 MiB/s, done.
Resolving deltas: 100% (99/99), done.


## 2. Install requirements

In [ ]:
%cd FACIAL/
!pip install -r requirements.txt
!pip install gdown

/content/FACIAL
     |████████████████████████████████| 26.6 MB 1.6 MB/s 
     |████████████████████████████████| 50 kB 6.6 MB/s 
  Created wheel for chumpy: filename=chumpy-0.70-py3-none-any.whl size=58285 sha256=267a225867c593b6e55a01efcd4217b5fe171f235069a485ed41cc22926b47cb
  Stored in directory: /root/.cache/pip/wheels/59/68/de/5e0c5d77e573e8c150e69e07a25035e6b6a04952d6e1814dbc
  Created wheel for torchfile: filename=torchfile-0.1.0-py3-none-any.whl size=5709 sha256=92eaa006fbf34c0160608e7b5d2758b87ca8af2bcbd8bb0d61afcc57aeb3c165
  Stored in directory: /root/.cache/pip/wheels/ac/5c/3a/a80e1c65880945c71fd833408cd1e9a8cb7e2f8f37620bb75b
  Created wheel for ffmpeg: filename=ffmpeg-1.4-py3-none-any.whl size=6084 sha256=3b75725f5953cca00cc990dc9edbac8fc3c0fc2a03646efe78cbcab9ecef4faf
  Stored in directory: /root/.cache/pip/wheels/64/80/6e/caa3e16deb0267c3cbfd36862058a724144e19fdb9eb03af0f
  Created wheel for python-speech-features: filename=python_speech_features-0.6-py3-none-any.whl s

In [ ]:
### Please download the pre-trained DeepSpeech model v0.1.0 from Mozilla (https://github.com/mozilla/DeepSpeech/releases/tag/v0.1.0) and place it in /content/FACIAL/audio2face/ds_graph.
# for audio features generation

!gdown -O /content/FACIAL/audio2face/ds_graph/output_graph.pb  https://drive.google.com/uc?id=1xsqUpHG6H8UJz0WB6Tp9xpQ1xYvmxuMK

Downloading...
From: https://drive.google.com/uc?id=1xsqUpHG6H8UJz0WB6Tp9xpQ1xYvmxuMK
To: /content/FACIAL/audio2face/ds_graph/output_graph.pb
100% 491M/491M [00:02<00:00, 205MB/s]


## 3. Data preprocess (~ 1h)

### 3.1 Download train video and test audio 

In [ ]:
################### Example includes:
# (1) train1.mp4（30 fps）, If your video is not 30 fps, you can use FFmpeg to convert FPS. For example: "ffmpeg -i train1.avi  -r 30 -b 5M  -y train1.mp4"
# (2) train1_image/, extracted images (h=w=512) for train1.mp4. 
# (3) train1_deep3Dface/, Deep3Dface reconstruction results, code: https://github.com/microsoft/Deep3DFaceReconstruction
# (4) train1_openface/, Openface result.
# (5) test1.wav (test audio)
!pip install gdown
!gdown -O video_preprocess.zip https://drive.google.com/uc?id=1NaB-yWEoJpyfAJc1KhHzxD0xvJCZiy_u
!unzip video_preprocess.zip

Streaming output truncated to the last 5000 lines.
  inflating: video_preprocess/train1_image/002560.jpg  
  inflating: video_preprocess/train1_image/002564.jpg  
  inflating: video_preprocess/train1_image/002596.jpg  
  inflating: video_preprocess/train1_image/002616.jpg  
  inflating: video_preprocess/train1_image/002648.jpg  
  inflating: video_preprocess/train1_image/002664.jpg  
  inflating: video_preprocess/train1_image/002681.jpg  
  inflating: video_preprocess/train1_image/002704.jpg  
  inflating: video_preprocess/train1_image/002762.jpg  
  inflating: video_preprocess/train1_image/002794.jpg  
  inflating: video_preprocess/train1_image/002843.jpg  
  inflating: video_preprocess/train1_image/002882.jpg  
  inflating: video_preprocess/train1_image/002965.jpg  
  inflating: video_preprocess/train1_image/002991.jpg  
  inflating: video_preprocess/train1_image/003009.jpg  
  inflating: video_preprocess/train1_image/003172.jpg  
  inflating: video_preprocess/train1_image/003283.jpg

### 3.2 Training data preprocess

In [ ]:
%cd face_render/face3d/mesh/cython
! python setup.py build_ext -i
%cd ../../../

### You have to download the BFM09 model and put it into /content/FACIAL/face_render/BFM subfolder. Following the instruction with https://github.com/microsoft/Deep3DFaceReconstruction
!mkdir BFM
!gdown -O /content/FACIAL/face_render/BFM/BFM_model_front.mat https://drive.google.com/uc?id=1Lp2UP4N5gBf26d_4IomIhyrlbZCV4Tvp
!gdown -O /content/FACIAL/face_render/BFM/std_exp.txt https://drive.google.com/uc?id=1V4ZtHcTMURQDJucCqpmSJtCKPBgcu5hN
# !cp /content/gdrive/MyDrive/FACIAL/BFM_model_front.mat /content/FACIAL/face_render/BFM/BFM_model_front.mat
# !cp /content/gdrive/MyDrive/FACIAL/std_exp.txt /content/FACIAL/face_render/BFM/std_exp.txt

/content/FACIAL/face_render/face3d/mesh/cython
running build_ext
skipping 'mesh_core_cython.cpp' Cython extension (up-to-date)
building 'mesh_core_cython' extension
creating build
creating build/temp.linux-x86_64-3.7
x86_64-linux-gnu-gcc -pthread -Wno-unused-result -Wsign-compare -DNDEBUG -g -fwrapv -O2 -Wall -g -fdebug-prefix-map=/build/python3.7-pX47U3/python3.7-3.7.12=. -fstack-protector-strong -Wformat -Werror=format-security -g -fdebug-prefix-map=/build/python3.7-pX47U3/python3.7-3.7.12=. -fstack-protector-strong -Wformat -Werror=format-security -Wdate-time -D_FORTIFY_SOURCE=2 -fPIC -I/usr/local/lib/python3.7/dist-packages/numpy/core/include -I/usr/include/python3.7m -c mesh_core_cython.cpp -o build/temp.linux-x86_64-3.7/mesh_core_cython.o
In file included from /usr/local/lib/python3.7/dist-packages/numpy/core/include/numpy/ndarraytypes.h:1822:0,
                 from /usr/local/lib/python3.7/dist-packages/numpy/core/include/numpy/ndarrayobject.h:12,
                 from /usr/loc

In [ ]:
! python handle_netface.py

In [ ]:
! python fit_headpose.py 

1000
2000
3000
4000
5000
6000
7000


In [ ]:
! python render_netface_fitpose.py

1000
2000
3000
4000
5000
6000
7000


### 3.3 Audio preprocess (CPU ~20m)

In [ ]:
!ffmpeg -i '/content/FACIAL/video_preprocess/train1.mp4' -acodec pcm_s16le -f wav -ac 1 -ar 16000  /content/FACIAL/video_preprocess/train1.wav

%cp -r /content/FACIAL/video_preprocess/train1.wav /content/FACIAL/examples/audio/train1.wav
%cp -r /content/FACIAL/video_preprocess/test1.wav /content/FACIAL/examples/audio/test1.wav


ffmpeg version 3.4.8-0ubuntu0.2 Copyright (c) 2000-2020 the FFmpeg developers
  built with gcc 7 (Ubuntu 7.5.0-3ubuntu1~18.04)
  configuration: --prefix=/usr --extra-version=0ubuntu0.2 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --enable-gpl --disable-stripping --enable-avresample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librubberband --enable-librsvg --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvorbis --enable-libvpx --enable-libwavpack --enable-libwebp --enable-libx265 --enable-libxml2 --enable-libxvid --enable-lib

In [ ]:
%cd /content/FACIAL/audio2face

! python audio_preprocessing.py

/content/FACIAL/audio2face




100% 1/1 [09:06<00:00, 546.82s/it]



## 3.1. Train audio2face

In [ ]:
%ls
!mkdir -p checkpoint/obama
!mkdir data
!pip install gdown
!gdown -O checkpoint/obama/Gen-20-0.0006273046686902202.mdl https://drive.google.com/uc?id=1NN5aH_R_OZFrCIQji1j-bpb5AETocBnf
!gdown -O data/train3.npz https://drive.google.com/uc?id=14mQo7U7VcwWxQ4y6EOC4vchmJBjbTYwB

audio_preprocessing.py*  ds_graph/                    model.py  _utils/
dataset102.py            fintuning2-trainheadpose.py  test.py
Downloading...
From: https://drive.google.com/uc?id=1NN5aH_R_OZFrCIQji1j-bpb5AETocBnf
To: /content/FACIAL/audio2face/checkpoint/obama/Gen-20-0.0006273046686902202.mdl
100% 38.8M/38.8M [00:00<00:00, 124MB/s] 
Downloading...
From: https://drive.google.com/uc?id=14mQo7U7VcwWxQ4y6EOC4vchmJBjbTYwB
To: /content/FACIAL/audio2face/data/train3.npz
100% 6.50M/6.50M [00:00<00:00, 102MB/s]


In [ ]:
%cd /content/FACIAL/audio2face
! python fintuning2-trainheadpose.py 

/content/FACIAL/audio2face
train1 train1_posenew
tensor(7071)
TfaceGAN(
  (model): UnetSkipConnectionBlock(
    (model): Sequential(
      (0): Conv1d(256, 256, kernel_size=(4,), stride=(2,), padding=(1,), bias=False)
      (1): UnetSkipConnectionBlock(
        (model): Sequential(
          (0): LeakyReLU(negative_slope=0.2, inplace=True)
          (1): Conv1d(256, 256, kernel_size=(4,), stride=(2,), padding=(1,), bias=False)
          (2): BatchNorm1d(256, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
          (3): UnetSkipConnectionBlock(
            (model): Sequential(
              (0): LeakyReLU(negative_slope=0.2, inplace=True)
              (1): Conv1d(256, 512, kernel_size=(4,), stride=(2,), padding=(1,), bias=False)
              (2): BatchNorm1d(512, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
              (3): UnetSkipConnectionBlock(
                (model): Sequential(
                  (0): LeakyReLU(negative_slope=0.2, inplace=Tr

## 3.2. Test audio2face

In [ ]:
%cd /content/FACIAL/audio2face
! python test.py --audiopath /content/FACIAL/examples/audio_preprocessed/test1.pkl --checkpath /content/FACIAL/audio2face/checkpoint/train1/Gen-10.mdl

/content/FACIAL/audio2face
/content/FACIAL/examples/audio_preprocessed/test1.pkl


## 4.1. Run 3D face rendering

In [ ]:
%cd /content/FACIAL/face_render/

! python rendering_gaosi.py --train_params_path /content/FACIAL/video_preprocess/train1_posenew.npz --net_params_path ../examples/test-result/test1.npz 

/content/FACIAL/face_render
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270


## 4.2. Prepare traning and testing data

In [ ]:
%cd ..
%cp -r /content/FACIAL/video_preprocess/train_A /content/FACIAL/face2vid/datasets/train3/train_A
%cp -r /content/FACIAL/video_preprocess/train1_image /content/FACIAL/face2vid/datasets/train3/train_B

%rm -rf /content/FACIAL/face2vid/datasets/train3/test_A /content/FACIAL/face2vid/datasets/train3/test_B
%cp -r /content/FACIAL/examples/rendering/test1 /content/FACIAL/face2vid/datasets/train3/test_A
%cp -r /content/FACIAL/examples/rendering/test1 /content/FACIAL/face2vid/datasets/train3/test_B

/content/FACIAL


##5.1.1 Download checkpoint for face2video (optional 1)

In [ ]:
%cd /content/FACIAL/face2vid
!mkdir -p checkpoints/train3/
!gdown -O checkpoints/train3/latest_net_G.pth https://drive.google.com/uc?id=1OZ5GUQnypQzmPHdZf3FWcxQ3fX2xkOnB

/content/FACIAL/face2vid
Downloading...
From: https://drive.google.com/uc?id=1OZ5GUQnypQzmPHdZf3FWcxQ3fX2xkOnB
To: /content/FACIAL/face2vid/checkpoints/train3/latest_net_G.pth
100% 354M/354M [00:02<00:00, 163MB/s]


##5.1.2 Train face2video by yourself (optional 2)

In [ ]:
### Please pay attention to modify blink_path when you train your own video. 
### Here we use 7200 images for training. (Usually 4000 images are enough.) 
%cd /content/FACIAL/face2vid
! python train.py --blink_path '../video_preprocess/train1_openface/train1_512_audio.csv' --name train3 --model pose2vid --dataroot ./datasets/train3/ --netG local --ngf 32 --num_D 3 --tf_log --niter_fix_global 0 --label_nc 0 --no_instance --save_epoch_freq 2 --lr=0.0001 --resize_or_crop resize --no_flip --verbose --n_local_enhancers 1

/content/FACIAL/face2vid
------------ Options -------------
batchSize: 1
beta1: 0.5
blink_path: ../video_preprocess/train1_openface/train1_512_audio.csv
checkpoints_dir: ./checkpoints
continue_train: False
data_type: 32
dataroot: ./datasets/train3/
debug: False
display_freq: 100
display_winsize: 512
feat_num: 3
fineSize: 512
gpu_ids: [0]
input_nc: 3
instance_feat: False
isTrain: True
label_feat: False
label_nc: 0
lambda_feat: 10.0
lambda_flow: 50.0
loadSize: 512
load_features: False
load_pretrain: 
lr: 0.0001
max_dataset_size: inf
model: pose2vid
nThreads: 4
n_blocks_global: 4
n_blocks_local: 3
n_clusters: 10
n_downsample_E: 4
n_downsample_global: 4
n_layers_D: 3
n_local_enhancers: 1
name: train3
ndf: 64
nef: 16
netG: local
ngf: 32
niter: 20
niter_decay: 30
niter_fix_global: 0
no_flip: True
no_flow_loss: False
no_ganFeat_loss: False
no_html: False
no_instance: True
no_lsgan: False
no_vgg_loss: False
norm: instance
num_D: 3
output_nc: 3
phase: train
pool_size: 0
print_freq: 100
resize_o

## 5.2 Test face2video

In [ ]:
! python test_video.py --test_id_name test1 --blink_path '../examples/test-result/test1.npz' --name train3 --model pose2vid --dataroot ./datasets/train3/ --which_epoch latest --netG local --ngf 32 --label_nc 0 --n_local_enhancers 1 --no_instance --resize_or_crop resize

------------ Options -------------
aspect_ratio: 1.0
batchSize: 1
checkpoints_dir: ./checkpoints
clip_length: 500
cluster_path: features_clustered_010.npy
data_type: 32
dataroot: ./datasets/train3/
display_winsize: 512
engine: None
export_onnx: None
feat_num: 3
fineSize: 512
gpu_ids: [0]
input_nc: 3
instance_feat: False
isTrain: False
label_feat: False
label_nc: 0
loadSize: 512
load_features: False
max_dataset_size: inf
model: pose2vid
nThreads: 4
n_blocks_global: 4
n_blocks_local: 3
n_clusters: 10
n_downsample_E: 4
n_downsample_global: 4
n_local_enhancers: 1
name: train3
nef: 16
netG: local
ngf: 32
niter_fix_global: 0
no_flip: False
no_instance: True
norm: instance
ntest: inf
onnx: None
output_nc: 3
phase: test
resize_or_crop: resize
results_dir: ./results/
serial_batches: False
test_id_name: test1
tf_log: False
use_dropout: False
use_first_frame: False
verbose: False
which_epoch: latest
-------------- End ----------------
CustomDatasetDataLoader
dataset [AlignedPairDataset] was creat

In [ ]:
import ffmpeg

audio_path ='/content/FACIAL/video_preprocess/test1.wav'
video_new='../examples/test_image/test1/test_1.avi'
output = '../examples/test_image/test1/test_1_audio.avi'
output_mp4 = '../examples/test_image/test1/test_1_audio.mp4'
!ffmpeg -i '$video_new' -i '$audio_path' -c copy '$output'
!ffmpeg -i '$output'  '$output_mp4'

ffmpeg version 3.4.8-0ubuntu0.2 Copyright (c) 2000-2020 the FFmpeg developers
  built with gcc 7 (Ubuntu 7.5.0-3ubuntu1~18.04)
  configuration: --prefix=/usr --extra-version=0ubuntu0.2 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --enable-gpl --disable-stripping --enable-avresample --enable-avisynth --enable-gnutls --enable-ladspa --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libgme --enable-libgsm --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librubberband --enable-librsvg --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libssh --enable-libtheora --enable-libtwolame --enable-libvorbis --enable-libvpx --enable-libwavpack --enable-libwebp --enable-libx265 --enable-libxml2 --enable-libxvid --enable-lib

## 6. Visualize the video result

In [ ]:
from IPython.display import HTML
from base64 import b64encode

mp4 = open(output_mp4, "rb").read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML(f"""
<video width="20%" height="20%" controls>
      <source src="{data_url}" type="video/mp4">
</video>""")